# Pommerman V4 Training in smaller central region

This notebook demonstrates how to train Pommerman agents. Please let us know at support@pommerman.com if you run into any issues.

In [1]:
import os
import sys
import numpy as np
import time

import pommerman
from pommerman.agents import SimpleAgent, RandomAgent, PlayerAgent, BaseAgent
from pommerman.configs import ffa_v4_fast_env
from pommerman.envs.v4 import Pomme as Pomme_v4
from pommerman.characters import Bomber
from pommerman import utility
from pommerman import agents
from pommerman import envs
from pommerman import constants
from pommerman import characters

# print all env configs
print(pommerman.REGISTRY)

['AdvancedLesson-v0', 'PommeFFACompetition-v0', 'PommeFFACompetitionFast-v0', 'PommeFFAFast-v0', 'PommeFFA-v1', 'PommeFFAFast-v3', 'PommeFFAFast-v4', 'PommeFFAFast-v5', 'Lesson1-v0', 'Lesson2-v0', 'Lesson2b-v0', 'Lesson2c-v0', 'Lesson2d-v0', 'Lesson2e-v0', 'Lesson3-v0', 'Lesson3b-v0', 'Lesson3c-v0', 'Lesson3d-v0', 'OneVsOne-v0', 'PommeRadioCompetition-v2', 'PommeRadio-v2', 'Simple-v0', 'SimpleRandomTeam-v0', 'SimpleTeam-v0', 'PommeTeamCompetition-v0', 'PommeTeamCompetitionFast-v0', 'PommeTeamCompetition-v1', 'PommeTeam-v0', 'PommeTeamFast-v0', 'PommeTeamSimple-v0']


# Train with stable baseline

In [2]:
import gym

from stable_baselines.common.policies import MlpPolicy
from stable_baselines.common.vec_env import SubprocVecEnv, DummyVecEnv
from stable_baselines import PPO2

/Users/kman/opt/anaconda3/envs/pommerman/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/Users/kman/opt/anaconda3/envs/pommerman/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/Users/kman/opt/anaconda3/envs/pommerman/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/Users/kman/opt/anaconda3/en

## Inherit pommerman env and make it compatible with stable-baseline

In [3]:
class CustomPomme(Pomme_v4):
    def __init__(self, **kwargs):
        super().__init__(**kwargs)
        self.obs_raw = None # store the raw version of observation
        self.training_idx = 1 # idx of the agent being trained
    
    # function to flatten pommerman observation
    def _transform_obs(self, obs_raw):
        obs_training = obs_raw[self.training_idx] # default the first agent to be trained

        # construct flattened observation
        obs = [
            *np.array(obs_training["board"]).reshape(-1),
            *np.array(obs_training["bomb_blast_strength"]).reshape(-1),
            *np.array(obs_training["bomb_life"]).reshape(-1),
            *np.array(obs_training["position"]).reshape(-1),
            obs_training["ammo"],
            obs_training["blast_strength"],
            obs_training["can_kick"],
            obs_training["teammate"].value,
            obs_training["enemies"][0].value,
            
            # uncommon if training 1 v 1
            obs_training["enemies"][0].value,
            obs_training["enemies"][0].value,
            
            # uncommon if training 2 v 2
#             obs_training["enemies"][1].value,
#             obs_training["enemies"][2].value,
        ]
        return obs
    
    def get_obs_raw(self):
        return self.obs_raw

    def step(self, action_training):
        action_nontraining = self.act(self.obs_raw)
        actions = [*action_nontraining, action_training]
        obs_raw, reward, done, info = super().step(actions)
        self.obs_raw = obs_raw
        return self._transform_obs(obs_raw), reward[self.training_idx], done, info
    
    def reset(self):
        obs_raw = super().reset()
        self.obs_raw = obs_raw
        return self._transform_obs(obs_raw)
    
    def render(self,
               mode=None,
               close=False,
               record_pngs_dir=None,
               record_json_dir=None,
               do_sleep=True):
        super().render(mode=mode,
                       close=close,
                       record_pngs_dir=record_pngs_dir,
                       record_json_dir=record_json_dir,
                       do_sleep=do_sleep)

In [4]:
# def team_v3_fast_env():
#     """Start up a FFA config with the default settings."""
#     env = CustomPomme
#     game_type = constants.GameType.Team
#     env_entry_point = 'CustomPomme'
#     env_id = 'PommeTeamFast-v3'
#     env_kwargs = {
#         'game_type': game_type,
#         'board_size': 8,
#         'num_rigid': 0,
#         'num_wood': 0,
#         'num_items': 0,
#         'max_steps': constants.MAX_STEPS,
#         'render_fps': 1000,
#         'env': env_entry_point,
#     }
#     agent = characters.Bomber
#     return locals()

# def one_vs_one_v3_env():
#     """Start up a FFA config with the default settings."""
#     env = CustomPomme
#     game_type = constants.GameType.OneVsOne
#     env_entry_point = 'CustomPomme'
#     env_id = 'PommeOneVsOneFast-v3'
#     env_kwargs = {
#         'game_type': game_type,
#         'board_size': 8,
#         'num_rigid': 0,
#         'num_wood': 0,
#         'num_items': 0,
#         'max_steps': constants.MAX_STEPS,
#         'render_fps': 1000,
#         'env': env_entry_point,
#     }
#     agent = characters.Bomber
#     return locals()

def one_vs_one_v4_env():
    """Start up a FFA config with the default settings."""
    env = CustomPomme
    game_type = constants.GameType.OneVsOne
    env_entry_point = 'CustomPomme'
    env_id = 'PommeOneVsOneFast-v4'
    env_kwargs = {
        'game_type': game_type,
        'board_size': 11,
        'free_board_size': 4,
        'num_rigid': 0,
        'num_wood': 0,
        'num_items': 0,
        'max_steps': constants.MAX_STEPS,
        'render_fps': 1000,
        'env': env_entry_point,
    }
    agent = characters.Bomber
    return locals()

In [6]:
#try to train against random agent who doesn't use bombs
from pommerman.agents.random_agent import RandomAgentNoBomb
# Instantiate the environment

config = one_vs_one_v4_env()
env_pom = CustomPomme(**config["env_kwargs"])

# config agents
agents = []
 
# Add simple agents
for agent_id in range(1):
    agents.append(RandomAgentNoBomb(config["agent"](agent_id, config["game_type"])))
    
# add player agent(to train)
agents.append(PlayerAgent(config["agent"](1, config["game_type"])))

env_pom.set_agents(agents)
env_pom.set_training_agent(agents[1].agent_id)
env_pom.set_init_game_state(None)

# Seed and reset the environment
env_pom.seed(0)

[0]

In [7]:
# log function during training, implement if needed
def log(local_var, global_var):
    pass
#     display(local_var)
#     display(global_var)

In [ ]:
# !!takes 48 hrs!!
import time
n_cpu = 2
env = DummyVecEnv([lambda: env_pom for i in range(n_cpu)])

model = PPO2(MlpPolicy, env, verbose=1, 
             n_steps = 3000, # batch_size = n_step * num_env
             ent_coef = 0.001, # entropy coefficient
             tensorboard_log="./ppo_pommerman_tensorboard/")
startTime = time.time()
model = model.learn(total_timesteps=300000000, # num_update = total_timesteps // batch_size
                    callback = log)
endTime = time.time()
elapsedTime = endTime - startTime
print(elapsedTime)
# model.save("ppo2_pommerman_20000_2")
# model = model.learn(total_timesteps=5000000, # num_update = total_timesteps // batch_size
#                     callback = log)
model.save("ppo2_pommerman_v4_4x4_randagentnobomb_300M")

In [13]:
model = PPO2.load("ppo2_pommerman_v4_4x4_randagentnobomb_300M")

n_cpu = 1
env = DummyVecEnv([lambda: env_pom for i in range(n_cpu)])
model.envs = env

# test the learned model
num_win = 0
num_tie = 0
num_lose = 0
total = 1000 # number of playouts
for i_episode in range(total):
    obs = env.reset()
    done = False
    info = None
    while not done:
#         env.render()
        action_training, _states = model.predict(obs)
#         print(action_training)
        obs, rewards, dones, infos = env.step(action_training)
#         print(infos)
        done = dones[0]
        info = infos[0]
#         time.sleep(0.0)
    print('Episode {} finished'.format(i_episode))
    if(info["result"].value == 0):
        if(1 in info["winners"]):
            num_win+=1
        else:
            num_lose+=1
    elif(info["result"].value == 2):
        num_tie+=1
#     print(info)
env.close()
print("Win ", num_win, "/", total, " games")
print("Tie ", num_tie, "/", total, " games")
print("Lose ", num_lose, "/", total, " games")


Loading a model without an environment, this model cannot be trained until it has a valid environment.
Episode 0 finished
Episode 1 finished
Episode 2 finished
Episode 3 finished
Episode 4 finished
Episode 5 finished
Episode 6 finished
Episode 7 finished
Episode 8 finished
Episode 9 finished
Episode 10 finished
Episode 11 finished
Episode 12 finished
Episode 13 finished
Episode 14 finished
Episode 15 finished
Episode 16 finished
Episode 17 finished
Episode 18 finished
Episode 19 finished
Episode 20 finished
Episode 21 finished
Episode 22 finished
Episode 23 finished
Episode 24 finished
Episode 25 finished
Episode 26 finished
Episode 27 finished
Episode 28 finished
Episode 29 finished
Episode 30 finished
Episode 31 finished
Episode 32 finished
Episode 33 finished
Episode 34 finished
Episode 35 finished
Episode 36 finished
Episode 37 finished
Episode 38 finished
Episode 39 finished
Episode 40 finished
Episode 41 finished
Episode 42 finished
Episode 43 finished
Episode 44 finished
Episode

Episode 395 finished
Episode 396 finished
Episode 397 finished
Episode 398 finished
Episode 399 finished
Episode 400 finished
Episode 401 finished
Episode 402 finished
Episode 403 finished
Episode 404 finished
Episode 405 finished
Episode 406 finished
Episode 407 finished
Episode 408 finished
Episode 409 finished
Episode 410 finished
Episode 411 finished
Episode 412 finished
Episode 413 finished
Episode 414 finished
Episode 415 finished
Episode 416 finished
Episode 417 finished
Episode 418 finished
Episode 419 finished
Episode 420 finished
Episode 421 finished
Episode 422 finished
Episode 423 finished
Episode 424 finished
Episode 425 finished
Episode 426 finished
Episode 427 finished
Episode 428 finished
Episode 429 finished
Episode 430 finished
Episode 431 finished
Episode 432 finished
Episode 433 finished
Episode 434 finished
Episode 435 finished
Episode 436 finished
Episode 437 finished
Episode 438 finished
Episode 439 finished
Episode 440 finished
Episode 441 finished
Episode 442 f

Episode 797 finished
Episode 798 finished
Episode 799 finished
Episode 800 finished
Episode 801 finished
Episode 802 finished
Episode 803 finished
Episode 804 finished
Episode 805 finished
Episode 806 finished
Episode 807 finished
Episode 808 finished
Episode 809 finished
Episode 810 finished
Episode 811 finished
Episode 812 finished
Episode 813 finished
Episode 814 finished
Episode 815 finished
Episode 816 finished
Episode 817 finished
Episode 818 finished
Episode 819 finished
Episode 820 finished
Episode 821 finished
Episode 822 finished
Episode 823 finished
Episode 824 finished
Episode 825 finished
Episode 826 finished
Episode 827 finished
Episode 828 finished
Episode 829 finished
Episode 830 finished
Episode 831 finished
Episode 832 finished
Episode 833 finished
Episode 834 finished
Episode 835 finished
Episode 836 finished
Episode 837 finished
Episode 838 finished
Episode 839 finished
Episode 840 finished
Episode 841 finished
Episode 842 finished
Episode 843 finished
Episode 844 f

In [24]:
#not bad, ~70% win rate. now try testing it in a 5x5 environment
def one_vs_one_v4_env():
    """Start up a FFA config with the default settings."""
    env = CustomPomme
    game_type = constants.GameType.OneVsOne
    env_entry_point = 'CustomPomme'
    env_id = 'PommeOneVsOneFast-v4'
    env_kwargs = {
        'game_type': game_type,
        'board_size': 11,
        'free_board_size': 5,
        'num_rigid': 0,
        'num_wood': 0,
        'num_items': 0,
        'max_steps': constants.MAX_STEPS,
        'render_fps': 1000,
        'env': env_entry_point,
    }
    agent = characters.Bomber
    return locals()

#try to train against random agent who doesn't use bombs
from pommerman.agents.random_agent import RandomAgentNoBomb
# Instantiate the environment

config = one_vs_one_v4_env()
env_pom = CustomPomme(**config["env_kwargs"])

# config agents
agents = []
 
# Add simple agents
for agent_id in range(1):
    agents.append(RandomAgentNoBomb(config["agent"](agent_id, config["game_type"])))
    
# add player agent(to train)
agents.append(PlayerAgent(config["agent"](1, config["game_type"])))

env_pom.set_agents(agents)
env_pom.set_training_agent(agents[1].agent_id)
env_pom.set_init_game_state(None)

# Seed and reset the environment
env_pom.seed(0)

[0]

In [26]:
#win rate in 6x6:
# Win  191 / 500  games
# Tie  49 / 500  games
# Lose  260 / 500  games

model = PPO2.load("ppo2_pommerman_v4_4x4_randagentnobomb_300M")

n_cpu = 1
env = DummyVecEnv([lambda: env_pom for i in range(n_cpu)])
model.envs = env

# test the learned model
num_win = 0
num_tie = 0
num_lose = 0
total = 500 # number of playouts
for i_episode in range(total):
    obs = env.reset()
    done = False
    info = None
    while not done:
#         env.render()
        action_training, _states = model.predict(obs)
#         print(action_training)
        obs, rewards, dones, infos = env.step(action_training)
#         print(infos)
        done = dones[0]
        info = infos[0]
#         time.sleep(0.1)
    print('Episode {} finished'.format(i_episode))
    if(info["result"].value == 0):
        if(1 in info["winners"]):
            num_win+=1
        else:
            num_lose+=1
    elif(info["result"].value == 2):
        num_tie+=1
#     print(info)
env.close()
print("Win ", num_win, "/", total, " games")
print("Tie ", num_tie, "/", total, " games")
print("Lose ", num_lose, "/", total, " games")


Loading a model without an environment, this model cannot be trained until it has a valid environment.
Episode 0 finished
Episode 1 finished
Episode 2 finished
Episode 3 finished
Episode 4 finished
Episode 5 finished
Episode 6 finished
Episode 7 finished
Episode 8 finished
Episode 9 finished
Episode 10 finished
Episode 11 finished
Episode 12 finished
Episode 13 finished
Episode 14 finished
Episode 15 finished
Episode 16 finished
Episode 17 finished
Episode 18 finished
Episode 19 finished
Episode 20 finished
Episode 21 finished
Episode 22 finished
Episode 23 finished
Episode 24 finished
Episode 25 finished
Episode 26 finished
Episode 27 finished
Episode 28 finished
Episode 29 finished
Episode 30 finished
Episode 31 finished
Episode 32 finished
Episode 33 finished
Episode 34 finished
Episode 35 finished
Episode 36 finished
Episode 37 finished
Episode 38 finished
Episode 39 finished
Episode 40 finished
Episode 41 finished
Episode 42 finished
Episode 43 finished
Episode 44 finished
Episode

Episode 395 finished
Episode 396 finished
Episode 397 finished
Episode 398 finished
Episode 399 finished
Episode 400 finished
Episode 401 finished
Episode 402 finished
Episode 403 finished
Episode 404 finished
Episode 405 finished
Episode 406 finished
Episode 407 finished
Episode 408 finished
Episode 409 finished
Episode 410 finished
Episode 411 finished
Episode 412 finished
Episode 413 finished
Episode 414 finished
Episode 415 finished
Episode 416 finished
Episode 417 finished
Episode 418 finished
Episode 419 finished
Episode 420 finished
Episode 421 finished
Episode 422 finished
Episode 423 finished
Episode 424 finished
Episode 425 finished
Episode 426 finished
Episode 427 finished
Episode 428 finished
Episode 429 finished
Episode 430 finished
Episode 431 finished
Episode 432 finished
Episode 433 finished
Episode 434 finished
Episode 435 finished
Episode 436 finished
Episode 437 finished
Episode 438 finished
Episode 439 finished
Episode 440 finished
Episode 441 finished
Episode 442 f

In [ ]:
#parameterize board size; run experiments on 300M agent


In [28]:
# train 6x6 agent
import time
n_cpu = 2
env = DummyVecEnv([lambda: env_pom for i in range(n_cpu)])
model = PPO2.load("ppo2_pommerman_v4_4x4_randagentnobomb_300M", env=env)
# model = PPO2(MlpPolicy, env, verbose=1, 
#              n_steps = 3000, # batch_size = n_step * num_env
#              ent_coef = 0.001, # entropy coefficient
#              tensorboard_log="./ppo_pommerman_tensorboard/")
# startTime = time.time()
model = model.learn(total_timesteps=50000000, # num_update = total_timesteps // batch_size
                    callback = log)
# endTime = time.time()
# elapsedTime = endTime - startTime
# print(elapsedTime)
# model.save("ppo2_pommerman_20000_2")
# model = model.learn(total_timesteps=5000000, # num_update = total_timesteps // batch_size
#                     callback = log)
model.save("ppo2_pommerman_v4_6x6_randagentnobomb_350M")

--------------------------------------
| approxkl           | 0.0011191944  |
| clipfrac           | 0.011541666   |
| explained_variance | -0.191        |
| fps                | 1679          |
| n_updates          | 1             |
| policy_entropy     | 0.079101235   |
| policy_loss        | -0.0020560191 |
| serial_timesteps   | 3000          |
| time_elapsed       | 3.1e-06       |
| total_timesteps    | 6000          |
| value_loss         | 0.21768048    |
--------------------------------------
--------------------------------------
| approxkl           | 0.0013381692  |
| clipfrac           | 0.013041667   |
| explained_variance | -0.127        |
| fps                | 1780          |
| n_updates          | 2             |
| policy_entropy     | 0.07860069    |
| policy_loss        | -0.0018632364 |
| serial_timesteps   | 6000          |
| time_elapsed       | 3.57          |
| total_timesteps    | 12000         |
| value_loss         | 0.17388475    |
-------------------------

--------------------------------------
| approxkl           | 0.0011425576  |
| clipfrac           | 0.008708334   |
| explained_variance | 0.0903        |
| fps                | 1752          |
| n_updates          | 18            |
| policy_entropy     | 0.074550465   |
| policy_loss        | -0.0016880357 |
| serial_timesteps   | 54000         |
| time_elapsed       | 58.1          |
| total_timesteps    | 108000        |
| value_loss         | 0.11264632    |
--------------------------------------
--------------------------------------
| approxkl           | 0.00092256715 |
| clipfrac           | 0.009333333   |
| explained_variance | 0.129         |
| fps                | 1810          |
| n_updates          | 19            |
| policy_entropy     | 0.07383001    |
| policy_loss        | -0.0011916622 |
| serial_timesteps   | 57000         |
| time_elapsed       | 61.5          |
| total_timesteps    | 114000        |
| value_loss         | 0.12407415    |
-------------------------

---------------------------------------
| approxkl           | 0.0006291069   |
| clipfrac           | 0.006833333    |
| explained_variance | 0.2            |
| fps                | 1839           |
| n_updates          | 35             |
| policy_entropy     | 0.07982224     |
| policy_loss        | -0.00090617157 |
| serial_timesteps   | 105000         |
| time_elapsed       | 114            |
| total_timesteps    | 210000         |
| value_loss         | 0.11374053     |
---------------------------------------
--------------------------------------
| approxkl           | 0.0012173433  |
| clipfrac           | 0.013249999   |
| explained_variance | 0.165         |
| fps                | 1839          |
| n_updates          | 36            |
| policy_entropy     | 0.08199759    |
| policy_loss        | -0.0015050418 |
| serial_timesteps   | 108000        |
| time_elapsed       | 118           |
| total_timesteps    | 216000        |
| value_loss         | 0.11674103    |
------------

--------------------------------------
| approxkl           | 0.0012788286  |
| clipfrac           | 0.010750001   |
| explained_variance | 0.215         |
| fps                | 1670          |
| n_updates          | 52            |
| policy_entropy     | 0.08560636    |
| policy_loss        | -0.0019686902 |
| serial_timesteps   | 156000        |
| time_elapsed       | 176           |
| total_timesteps    | 312000        |
| value_loss         | 0.10944824    |
--------------------------------------
--------------------------------------
| approxkl           | 0.000984978   |
| clipfrac           | 0.010875001   |
| explained_variance | 0.187         |
| fps                | 1688          |
| n_updates          | 53            |
| policy_entropy     | 0.08128755    |
| policy_loss        | -0.0012521845 |
| serial_timesteps   | 159000        |
| time_elapsed       | 180           |
| total_timesteps    | 318000        |
| value_loss         | 0.118881255   |
-------------------------

--------------------------------------
| approxkl           | 0.0006601051  |
| clipfrac           | 0.00575       |
| explained_variance | 0.24          |
| fps                | 1813          |
| n_updates          | 69            |
| policy_entropy     | 0.072881535   |
| policy_loss        | -0.0011265535 |
| serial_timesteps   | 207000        |
| time_elapsed       | 236           |
| total_timesteps    | 414000        |
| value_loss         | 0.11116536    |
--------------------------------------
--------------------------------------
| approxkl           | 0.00045781038 |
| clipfrac           | 0.0045000003  |
| explained_variance | 0.188         |
| fps                | 1806          |
| n_updates          | 70            |
| policy_entropy     | 0.071941495   |
| policy_loss        | -0.0009040907 |
| serial_timesteps   | 210000        |
| time_elapsed       | 239           |
| total_timesteps    | 420000        |
| value_loss         | 0.11612852    |
-------------------------

...

---------------------------------------
| approxkl           | 0.000219117    |
| clipfrac           | 0.0010416667   |
| explained_variance | 0.554          |
| fps                | 1841           |
| n_updates          | 8269           |
| policy_entropy     | 0.0070020743   |
| policy_loss        | -2.2815631e-05 |
| serial_timesteps   | 24807000       |
| time_elapsed       | 2.69e+04       |
| total_timesteps    | 49614000       |
| value_loss         | 0.09092503     |
---------------------------------------
---------------------------------------
| approxkl           | 0.00019840525  |
| clipfrac           | 0.0011250001   |
| explained_variance | 0.532          |
| fps                | 1853           |
| n_updates          | 8270           |
| policy_entropy     | 0.007973657    |
| policy_loss        | -0.00025952648 |
| serial_timesteps   | 24810000       |
| time_elapsed       | 2.69e+04       |
| total_timesteps    | 49620000       |
| value_loss         | 0.095818706    |


---------------------------------------
| approxkl           | 0.0010703163   |
| clipfrac           | 0.004041667    |
| explained_variance | 0.557          |
| fps                | 1853           |
| n_updates          | 8285           |
| policy_entropy     | 0.010937326    |
| policy_loss        | -0.00060816354 |
| serial_timesteps   | 24855000       |
| time_elapsed       | 2.69e+04       |
| total_timesteps    | 49710000       |
| value_loss         | 0.08702653     |
---------------------------------------
--------------------------------------
| approxkl           | 0.0021167044  |
| clipfrac           | 0.004916666   |
| explained_variance | 0.551         |
| fps                | 1861          |
| n_updates          | 8286          |
| policy_entropy     | 0.013460159   |
| policy_loss        | -0.0002831827 |
| serial_timesteps   | 24858000      |
| time_elapsed       | 2.69e+04      |
| total_timesteps    | 49716000      |
| value_loss         | 0.0902384     |
------------

---------------------------------------
| approxkl           | 0.0006852023   |
| clipfrac           | 0.0027500002   |
| explained_variance | 0.565          |
| fps                | 1840           |
| n_updates          | 8301           |
| policy_entropy     | 0.013230442    |
| policy_loss        | -0.00038431532 |
| serial_timesteps   | 24903000       |
| time_elapsed       | 2.7e+04        |
| total_timesteps    | 49806000       |
| value_loss         | 0.09021614     |
---------------------------------------
--------------------------------------
| approxkl           | 0.00085857743 |
| clipfrac           | 0.006458333   |
| explained_variance | 0.519         |
| fps                | 1855          |
| n_updates          | 8302          |
| policy_entropy     | 0.015277855   |
| policy_loss        | -0.0004296937 |
| serial_timesteps   | 24906000      |
| time_elapsed       | 2.7e+04       |
| total_timesteps    | 49812000      |
| value_loss         | 0.094113916   |
------------

--------------------------------------
| approxkl           | 0.00082408555 |
| clipfrac           | 0.0042499998  |
| explained_variance | 0.577         |
| fps                | 1791          |
| n_updates          | 8317          |
| policy_entropy     | 0.012220379   |
| policy_loss        | -0.0001616619 |
| serial_timesteps   | 24951000      |
| time_elapsed       | 2.7e+04       |
| total_timesteps    | 49902000      |
| value_loss         | 0.08776452    |
--------------------------------------
---------------------------------------
| approxkl           | 0.00072791247  |
| clipfrac           | 0.0025416669   |
| explained_variance | 0.531          |
| fps                | 1837           |
| n_updates          | 8318           |
| policy_entropy     | 0.0117847705   |
| policy_loss        | -0.00035803538 |
| serial_timesteps   | 24954000       |
| time_elapsed       | 2.7e+04        |
| total_timesteps    | 49908000       |
| value_loss         | 0.09730203     |
-------------

---------------------------------------
| approxkl           | 0.0008403093   |
| clipfrac           | 0.0024166668   |
| explained_variance | 0.531          |
| fps                | 1862           |
| n_updates          | 8333           |
| policy_entropy     | 0.010584555    |
| policy_loss        | -0.00069606106 |
| serial_timesteps   | 24999000       |
| time_elapsed       | 2.71e+04       |
| total_timesteps    | 49998000       |
| value_loss         | 0.09884847     |
---------------------------------------
